# Getting Started with MonoDAQ

We will walk you through the basic usage of python API, like how to:

1. setup channels, 
2. fetch values, 
3. plot it, 
4. add a math channel and 
5. run it as a real-time scope with a rising edge trigger.

## Wiring

In this demo we shall activate an analog, a digital one and a PWM channel, then wire the 
PWM output (from pin 4) back to the digital input (pin 1).

## 1. Setup Channels

First we call the `reset()` function to begin from the start, then we configure the channels, and print out the configuration. The configuration could also be stored in a 1-wire memory attached to a connector that is automatically reloaded when the connector with such a memory is detected.

When directly accessing the parameters, you may want to use the Parameters view of the IDM, which will help you browse through the device data structure.

In [1]:
from isotel.idm import monodaq, signal, gateway

mdu = monodaq.MonoDAQ_U()
mdu.reset()

mdu['ch.function.function3'] = 'PWM'
mdu['ch.rate.rate3'] = 1200
mdu['ch.set.set3'] = 0.25

mdu['ch.function.function0'] = 'Digital Input'
mdu['ch.function.function2'] = 'Voltage Input'
mdu['ch.rate.rate2'] = 50000

mdu.wait4ready()
mdu.print_setup()

## 2. Acquire Only

The `MonoDAQ_U.fetch()` method is a python generator and fetches N samples from analog channels or digital ones if the analog channels are not active to return the **stream** of tuples organized as:

- tuples of independent streams,
- each stream holds time (x-axis) and the tuple of channels synchronous to the time (y-axis),

For example: 

- `s[0][1][0]` means from stream0, channels, and select 0-th channel

The generator provides meta information on the channels in the first line (row). In order to fetch the values, the generators need a sink, which loops over all the entries. In our example, we simply use the `list()` as the sink to display values.

From the channel setup above, we can see that digital samples run twice as fast as analog ones. However since `N` primarily selects analog samples, the following example will put twice the number of digital samples compared to analog ones:

In [2]:
list( mdu.fetch(N=3) )

[(('t [s]', ('V1+ [V]',)), ('t [s]', ('DI1 [V]',))),
 ((0.0, (0.13,)), (0.0, (1,))),
 ((None, (nan,)), (1e-05, (1,))),
 ((2e-05, (0.1275,)), (2e-05, (1,))),
 ((None, (nan,)), (3e-05, (1,))),
 ((4e-05, (0.1102,)), (4e-05, (1,)))]

## 3. Plot

The `fetch()` method outputs a stream. To be able to plot it, the stream must be collected into a **signal**. A signal here means a dict sorted by channels, each having a pair of lists of equal size, providing Y samples and corresponding X time samples.

To convert the generated output to a stream use the `signal.stream2signal()` method, which is a generator returning signals. 

By extending this example we get a nicely sorted dict; again we use the `list()` to display the results. We may again observe more digital samples than analog ones, however, the time axis fits together nicely:

In [3]:
list( signal.stream2signal( mdu.fetch(3) ))

[{'DI1 [V]': {'x': [0.0, 1e-05, 2e-05, 3e-05, 4e-05], 'y': [0, 0, 0, 0, 0]},
  'V1+ [V]': {'x': [0.0, 2e-05, 4e-05], 'y': [0.0006, -0.0001, 0.0011]}}]

Now to the plot, with the `signal.scope()` which iterates over signals provided by the `stream2signal()` method and returns last acquired signal as data. Let us increase the number of samples to get a nicer waveform.

In [4]:
signal.scope( signal.stream2signal( mdu.fetch(100) ), title = 'First Plot');

Loading BokehJS ...

## 4. Adding a Math Channel

It would be a pity not to be able to perform a real-time analysis or computation on data in python.
We mute the first `V1+ [V]` channel and change the colors of the other two. You may freely enter
an equation with channel names with big capital letters, and only up to the + sign or space.

In [5]:
signal.scope(
    signal.stream2signal(
        signal.addmath( mdu.fetch(100), 'Masked [V]', expr = '5*V1*DI1'),
    ), title = 'First Plot with Math Channel', colors = [ None, 'darkgreen', 'darkorange']);

Loading BokehJS ...

## 5. Real-time Scope

Real-time updates require that a larger continuous stream of samples is fetched from the MonoDAQ. We achieve that by providing `fetch(2000000)` a sufficiently big number to run for some more time.

To display the intermediate collected samples, we need to instruct the `stream2signal()` a `split` parameter with a number of samples to be displayed in one shot. Note that `fetch()` refers to analog samples and there may be a significantly larger number of digital samples at the output. In addition if you want, you can reset the time and start at zero each time a shot is made. Then you should set the `relative_time` to True.

And last, we introduce a rising edge trigger function `signal.trigger`, which evaluates:

- The precondition that must be met in order to search for a
- trigger condition.
- Trigger is set a `single_shot` mode by default.

The example below shows how to wait for a rising edge on the `DI1` digital channel by specifying both the pre-condition and the condition. When the condition triggers, `P` pre-buffered samples are yielded and then continues for the remaining `N` samples.

In [6]:
data = signal.scope(
    signal.stream2signal(
        signal.trigger( mdu.fetch(2000000), precond='DI1 < 0.5', cond='DI1 > 0.5',
                        P=200, N=200, single_shot=False, post_delay = 0.1),
        split=400, relative_time=True),
    title="Continous Mode - Rising Edge Trigger", y_range = (-0.1,1.1) )
if not data:
    print('Signal not detected')

Loading BokehJS ...